In [1]:
from datasets import load_dataset
import pandas as pd

# Step 1: Load the dataset from HuggingFace
ds = load_dataset("jkhedri/psychology-dataset")

# Step 2: Convert the dataset to a Pandas DataFrame
train_df = ds["train"].to_pandas()

# Step 3: Remove the third column
train_df = train_df.drop(columns=train_df.columns[2])  # Drops the third column

# Step 4: Save the modified DataFrame to a CSV file
csv_file_path = "psychology_dataset.csv"

c:\Users\midhu\llamaindexproject\GeminiAI\geminiai\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Step 4: Save the modified DataFrame to a CSV file
train_df.to_csv(csv_file_path, index=False)  # Set index=False to avoid saving the index as a column


In [3]:
from langchain_community.document_loaders.csv_loader import CSVLoader

In [4]:
# Step 5: Load the CSV file using LangChain's CSVLoader
loader = CSVLoader(file_path=csv_file_path)

In [5]:
documents = loader.load()
for document in documents:
    print(document)

page_content='question: I'm feeling really anxious lately and I don't know why.
response_j: It's common to feel anxious at times, and there can be many reasons for it. Have there been any recent changes or stressors in your life that may be contributing to your anxiety? Let's work together to identify any triggers and develop coping strategies to manage your anxiety.' metadata={'source': 'psychology_dataset.csv', 'row': 0}
page_content='question: I think my partner may be cheating on me. What should I do?
response_j: It's understandable to feel worried and suspicious in this situation. Have you talked to your partner about your concerns? It's important to communicate openly and honestly with them. If you're still feeling uncertain, we can work on developing a plan to address the situation in a healthy and constructive way.' metadata={'source': 'psychology_dataset.csv', 'row': 1}
page_content='question: I'm feeling really overwhelmed with work and school. I don't know how to manage my t

In [6]:
from langchain.text_splitter import RecursiveCharacterTextSplitter


In [7]:
#Split the Data into Text Chunks
def text_split(documents):
    text_splitter=RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
    text_chunks=text_splitter.split_documents(documents)
    return text_chunks

In [8]:
text_chunks=text_split(documents)
print("Length of Text Chunks", len(text_chunks))

Length of Text Chunks 10994


In [9]:
# Display the text chunks
for i, chunk in enumerate(text_chunks):
    print(f"Chunk {i + 1}:\n{chunk.page_content}\n")

Chunk 1:
question: I'm feeling really anxious lately and I don't know why.
response_j: It's common to feel anxious at times, and there can be many reasons for it. Have there been any recent changes or stressors in your life that may be contributing to your anxiety? Let's work together to identify any triggers and develop coping strategies to manage your anxiety.

Chunk 2:
question: I think my partner may be cheating on me. What should I do?
response_j: It's understandable to feel worried and suspicious in this situation. Have you talked to your partner about your concerns? It's important to communicate openly and honestly with them. If you're still feeling uncertain, we can work on developing a plan to address the situation in a healthy and constructive way.

Chunk 3:
question: I'm feeling really overwhelmed with work and school. I don't know how to manage my time and it's causing me a lot of stress.
response_j: It sounds like you're going through a difficult time. Let's work on creati

In [10]:
from langchain.embeddings import HuggingFaceEmbeddings

In [11]:
#Download the Embeddings from Hugging Face
def download_hugging_face_embeddings():
    embeddings=HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')
    return embeddings

In [12]:
embeddings = download_hugging_face_embeddings()

C:\Users\midhu\AppData\Local\Temp\ipykernel_32472\2661704553.py:3: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings=HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')


In [13]:
query_result = embeddings.embed_query("Hello world")
print("Length", len(query_result))

Length 384


In [16]:
pip install load_dotenv

Note: you may need to restart the kernel to use updated packages.


In [20]:
from pinecone.grpc import PineconeGRPC as Pinecone
from pinecone import ServerlessSpec
import os

pc = Pinecone(api_key="pcsk_4Y21ba_6pss1wm8jyttfpnEAY6sB5Jrqa9dmgdM61d93zQCLpCSF9Yp7Bi4vL1GMhRDJBn")

index_name = "supportagent"


pc.create_index(
    name=index_name,
    dimension=384, 
    metric="cosine", 
    spec=ServerlessSpec(
        cloud="aws", 
        region="us-east-1"
    ) 
) 

In [21]:
import os
os.environ["PINECONE_API_KEY"] = "pcsk_4Y21ba_6pss1wm8jyttfpnEAY6sB5Jrqa9dmgdM61d93zQCLpCSF9Yp7Bi4vL1GMhRDJBn"

In [22]:
# Embed each chunk and upsert the embeddings into your Pinecone index.
from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_documents(
    documents=text_chunks,
    index_name=index_name,
    embedding=embeddings, 
)

In [23]:
# Load Existing index 

from langchain_pinecone import PineconeVectorStore
# Embed each chunk and upsert the embeddings into your Pinecone index.
docsearch = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embeddings
)

In [24]:
docsearch

In [25]:
retriever = docsearch.as_retriever(search_type="similarity", search_kwargs={"k":3})

In [26]:
retrieved_docs = retriever.invoke("I'm trouble having sleep,Can u help me for that?")

In [27]:
retrieved_docs

[Document(id='18b446b4-fd54-493a-bf49-56f6b3cff6fa', metadata={'row': 8767.0, 'source': 'psychology_dataset.csv'}, page_content="question: I'm having trouble sleeping, what should I do?"),
 Document(id='de120f5e-ec34-4f23-b084-32323d2e5e19', metadata={'row': 996.0, 'source': 'psychology_dataset.csv'}, page_content="question: I'm having trouble sleeping and I don't know what to do.\nresponse_j: Let's discuss any lifestyle habits or stressors that may be affecting your sleep. We can also explore relaxation techniques and potentially refer you to a sleep specialist if necessary."),
 Document(id='686ee6f1-1c3e-4ab5-8b89-066c8d60e471', metadata={'row': 6649.0, 'source': 'psychology_dataset.csv'}, page_content="question: I'm having trouble sleeping. What can I do about it?\nresponse_j: There are many things that can help with sleep, such as practicing good sleep hygiene, establishing a consistent sleep schedule, and avoiding caffeine and technology before bed. It may also be helpful to talk 

In [28]:
pip install langchain-groq


Note: you may need to restart the kernel to use updated packages.


In [205]:
import os
os.environ["GROQ_API_KEY"] = "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"

In [206]:
from langchain_groq import ChatGroq
from langchain_core.prompts import ChatPromptTemplate
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain

In [207]:
# Initialize Groq LLM
llm = ChatGroq(
    model_name="llama-3.3-70b-versatile",
    temperature=1
)


In [209]:
system_prompt = (
    """You are a compassionate and friendly chatbot. Respond thoughtfully and kindly to the following question 
    using ONLY the provided context. If the context does not contain enough information to answer, 
    politely say, 'I'm sorry, but I don't have enough information to answer that.'
    {context}"""
)








prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        ("human", "{input}"),
    ]
)

In [210]:
question_answer_chain = create_stuff_documents_chain(llm, prompt)
rag_chain = create_retrieval_chain(retriever, question_answer_chain)

In [157]:
response = rag_chain.invoke({"input": "I'm having trouble sleeping and it's affecting my daily life."})
print(response["answer"])

I'm so sorry to hear that you're struggling with sleep and it's impacting your daily life. That can be really frustrating and exhausting. There are many potential reasons for sleep difficulties, and it might be helpful to explore some possible causes together. 

Can you tell me a bit more about what's been going on with your sleep? For example, are you having trouble falling asleep, staying asleep, or waking up too early? Have you noticed any patterns or triggers that might be contributing to your sleep issues? Additionally, have you tried any strategies or techniques to help improve your sleep, such as establishing a bedtime routine or creating a relaxing sleep environment?


In [218]:
response = rag_chain.invoke({"input": "My girfriend drinks too much,I am not able to restrict her from this habit.Can u help me with this?"})
print(response["answer"])

I can sense your concern for your girlfriend's well-being. It's great that you want to support her in a positive way. Approaching the situation with care and compassion is key. 

You might want to consider having an open and honest conversation with your girlfriend, expressing your concerns about her drinking in a non-judgmental way. Let her know how her behavior is affecting you and your relationship. It's essential to listen to her perspective and feelings as well.

It's also important to recognize that you can't force someone to change their habits, but you can offer support and encouragement. You could suggest seeking professional help together, such as couples therapy or counseling, to address any underlying issues that might be contributing to her drinking.

Additionally, you can offer to help her find resources such as support groups or a licensed therapist who specializes in addiction. Being a supportive partner can make a significant difference in her journey towards a healthi

In [212]:
response = rag_chain.invoke({"input": "Give me a code for tic-tactor game"})
print(response["answer"])

I'm sorry, but I don't have enough information to answer that.
